[View in Colaboratory](https://colab.research.google.com/github/msakarvadia/C/blob/master/Naive_Bayes_Classificaiton_Document_Classification.ipynb)

#Probability and Statistics for AI & Machine Learning**
## Document Classification using Naive Bayes Classifier.

 NC State University


This code classifies the sentiment of IMDB movie reviews using a Naive Bayes Classifier. Because of the nature of this classifier our accuracy for classificiations will only hit around 80-85% due to our "naive" assumption that there are no dependencies between words in a moive review.

# Dataset 

In [0]:
from keras.datasets import imdb
(x_train, y_train), (x_test, y_test) = imdb.load_data(path="imdb.npz",
                                                      num_words=None,
                                                      skip_top=0,
                                                      maxlen=None,
                                                      seed=113,
                                                      start_char=1,
                                                      oov_char=2,
                                                      index_from=3)

Using TensorFlow backend.


17465344/17464789 [==============================] - 1s 0us/step


In [0]:
print(x_test[10:40])

[list([1, 1581, 34, 7908, 5082, 23, 6, 1374, 1120, 7, 107, 349, 18096, 1496, 11, 5116, 18, 397, 3767, 7, 4, 107, 84, 6763, 56, 68, 456, 1402, 21085, 39, 4, 1374, 9, 35, 204, 5, 55, 4412, 212, 193, 23, 4, 326, 45, 6, 1109, 8, 1738, 13214, 15, 29, 199, 1040, 5, 2684, 11, 14, 1403, 212, 1528, 10, 10, 2160, 16444, 9, 4, 452, 37, 10101, 4, 598, 425, 5, 45, 4394, 138, 59, 214, 467, 4, 2391, 7, 1738, 13214, 19, 41, 2455, 3028, 5, 6866, 1489, 90, 180, 18, 101, 1403, 41267, 1514, 5257, 9, 4, 564, 871, 322, 47, 2586, 27, 274, 326, 5, 9, 150, 112, 87284, 17, 6, 87, 162, 2133, 60, 3256, 23, 4, 7999, 123, 8, 11, 28676, 29, 144, 30, 2961, 1346, 13214, 214, 4, 326, 7, 18096, 1496, 8, 3767, 533, 7, 134, 16978, 6229, 10, 10, 7, 265, 285, 5, 233, 70, 593, 54, 564, 4124, 18136, 1625, 27, 1546, 15480, 19, 20558, 1008, 18, 89, 4, 114, 3209, 5, 45, 1139, 32, 4, 96, 143, 3760, 958, 7, 919, 5, 7611, 367, 4, 96, 17, 73, 17, 6, 52, 855, 7, 836, 10, 10, 18, 20854, 7, 328, 212, 14, 31, 9, 5523, 8, 591])
 list([1,

In [0]:
import numpy as np
import pandas as pd
import math

In [0]:
#determine total number of words in all positive documents and total words in negative documents
oneWordCount = 0
zeroWordCount = 0
for i in range(25000):
  if y_train[i]==1:
    oneWordCount += len(x_train[i])
  else:
    zeroWordCount += len(x_train[i])
  
      
print(oneWordCount)
print(zeroWordCount)

3019537
2948304


In [0]:
#2 column array of [word, frequency] of one classified documents
oneWordFreq = {}
zeroWordFreq = {}

#determine the fequency of each word in 1 classified documents and 0 classified documents and append values to frequency array defined above
for i in range(25000):
  if y_train[i] == 1:
    for w in range(len(x_train[i])):
      oneWordFreq[x_train[i][w]] = oneWordFreq.get(x_train[i][w],0)+1
  if y_train[i] ==0:
    for w in range(len(x_train[i])):
      zeroWordFreq[x_train[i][w]] = zeroWordFreq.get(x_train[i][w],0)+1

In [0]:
#checks to make sure that the frequency counter is accuratly counting frequencies by summing all of them up and seeing if they match the total word count
total = 0
a=0
for k,v in oneWordFreq.items():
  total += v
  a+=1
print(total)

totalTwo = 0
for k,v in zeroWordFreq.items():
  totalTwo += v
print(totalTwo)

3019537
2948304


In [0]:
#In order to account for words in the test set that arnt in the training set we will use a laplace function
#add 10,000 to the total word count; this is our assumption for the amount of vocab words possible
oneWordCount += 10000
zeroWordCount += 10000

#to complete the laplace funciton, we add one to the frequency of of all words
for k,v in oneWordFreq.items():
  oneWordFreq[k]= v+1
  
for k,v in zeroWordFreq.items():
  zeroWordFreq[k]= v+1

In [0]:
#we must now assume that the probablity of words occuring are independant...this is an untrue and naive assumption but we need this to simplfy things and use conditional probability
#P(word|Classification) = Freq of word + 1 / Total # of words + 10000

for k,v in oneWordFreq.items():
  oneWordFreq[k]= v/oneWordCount
for a,b in zeroWordFreq.items():
  zeroWordFreq[a] = b/zeroWordCount

In [0]:
print(sorted(oneWordFreq.items(), key=lambda s: s[0]))

[(1, 0.00412637310585743), (4, 0.05710146467925627), (5, 0.029615086397690473), (6, 0.02761775149139951), (7, 0.025367242585253125), (8, 0.022028448571514394), (9, 0.01889364612480389), (10, 0.0162519883401325), (11, 0.016569198527695818), (12, 0.012994064769633116), (13, 0.011981038686769628), (14, 0.011576686470572896), (15, 0.011292154543747114), (16, 0.00723245829313192), (17, 0.008682844936371465), (18, 0.0073981601809121325), (19, 0.007673119687925911), (20, 0.0062240533784535396), (21, 0.006872007174693691), (22, 0.006722809459003142), (23, 0.0056124087608106455), (24, 0.0047086402971807245), (25, 0.0048624591810563795), (26, 0.004887215439190873), (27, 0.005685357201446954), (28, 0.004154430198409856), (29, 0.0048759926021699025), (30, 0.00409798592986321), (31, 0.004454806130441714), (32, 0.003936905210268103), (33, 0.0037078273016635877), (34, 0.003959350884310045), (35, 0.0037236713068696634), (36, 0.0030390782485904613), (37, 0.0036289373590750007), (38, 0.00301861307519928

In [0]:
print(sorted(zeroWordFreq.items(), key=lambda s: s[0]))

[(1, 0.004225732041061365), (2, 6.760630415264963e-07), (4, 0.0551528848962108), (5, 0.025142446482849634), (6, 0.026830575897541294), (7, 0.023323498869622594), (8, 0.023315386113124278), (9, 0.016927266433740415), (10, 0.01779296515841509), (11, 0.01478516068666371), (12, 0.013417823185176371), (13, 0.013807573528616397), (14, 0.013826841325299901), (15, 0.012026823477235606), (16, 0.00888549655478274), (17, 0.0069715620842212295), (18, 0.007411003061213452), (19, 0.007057422090495095), (20, 0.008352758878059861), (21, 0.0073613124276612546), (22, 0.006331330383895637), (23, 0.005809747747357946), (24, 0.0055258012699168175), (25, 0.005120501476521683), (26, 0.004942358865079451), (27, 0.004105054788148885), (28, 0.005118473287397104), (29, 0.004117899985937889), (30, 0.004913288154293811), (31, 0.0044008323688167275), (32, 0.004065843131740348), (33, 0.004149674948889634), (34, 0.0035648804179692147), (35, 0.0034678653715101626), (36, 0.004034068168788603), (37, 0.003247468819972524

In [0]:
# if there is a new word in the test set, eventhough we have the laplace function, the probability will still approach zero since we are multiplying; instead we take the log of each individual probbility and add them
negChecker = 0
for k,v in oneWordFreq.items():
  oneWordFreq[k]= math.log(v)
for k,v in zeroWordFreq.items():
  zeroWordFreq[k]= math.log(v)

In [0]:
print(oneWordFreq.items())

dict_items([(1, -5.4903564404385445), (14, -4.45876199022142), (22, -5.0022491375593505), (16, -4.929176287721427), (43, -6.049892237972773), (530, -8.093046125882928), (973, -9.200335258576727), (1622, -9.788121923478846), (1385, -9.58638228082779), (65, -6.112119136590356), (458, -8.467150704956945), (4468, -10.898568669793958), (66, -6.315972805844406), (3941, -10.863477349982688), (4, -2.8629255115238283), (173, -7.275657329627188), (36, -5.796201017241262), (256, -7.563816387539956), (5, -3.519471371894963), (25, -5.3262109647141695), (100, -6.859283884754885), (838, -9.1493688149847), (112, -6.84802673023025), (50, -6.0913326580945535), (670, -8.580039926402776), (22665, -12.978010211473794), (9, -3.968929597311817), (35, -5.593045186924187), (480, -7.958840014927701), (284, -7.852346996317576), (150, -7.1558099820031185), (172, -7.336609854506492), (167, -7.362278614940328), (21631, -12.844478818849272), (336, -7.771651504496568), (385, -8.130454227949098), (39, -5.6394934452002

In [0]:
print(zeroWordFreq.items())

dict_items([(1, -5.466562769024964), (194, -7.490990245195399), (1153, -9.21995408009846), (8255, -11.46613948463038), (78, -5.994275507907506), (228, -7.720818719611493), (5, -3.683197766201165), (6, -3.618213150088374), (1463, -9.436294884089918), (4369, -11.138926573421966), (5012, -11.211247235001592), (134, -6.989902982018183), (26, -5.309912558698089), (4, -2.8976462246559898), (715, -8.795333456700542), (8, -3.7586417881416616), (118, -7.2542508639307135), (1634, -9.6322685300522), (14, -4.281143552355692), (394, -7.6623484971920846), (20, -4.785163390132872), (13, -4.282538030936669), (119, -7.242371417980662), (954, -8.893773529513794), (189, -7.236719024222048), (102, -6.589219931947077), (207, -7.400150148163406), (110, -6.809111647404996), (3103, -10.50567753444309), (21, -4.911517043162577), (69, -6.17722098811476), (188, -7.323516922142489), (30, -5.3158118761225515), (23, -5.14821812603884), (7, -3.7582938914634654), (249, -7.08491962692644), (126, -6.810644214754774), (

In [0]:
#for every review we calculate the total sum of all of the oneWordFreq of indepentant word probabilites and sum them up and do the same for zeroWordFreq
#compare which one is greater for each line...and voila that is your class

#we will have to still check that keys are in range and if not do 1/__WordCount

def oneTrainer(x_train, y_train):
  oneProb = []
  for i in range(25000):
      oneRowProb = 0
      zeroRowProb = 0
      for w in x_train[i]:
        word = w
        if w in oneWordFreq.keys():
          oneRowProb += oneWordFreq[word]
        else:
          oneRowProb += math.log(1/oneWordCount)
      oneProb.append(oneRowProb)
  return oneProb

In [0]:
def zeroTrainer(x_train, y_train):
  zeroProb = []
  for i in range(25000):
      oneRowProb = 0
      zeroRowProb = 0
      for w in x_train[i]:
        word = w    
        if w in zeroWordFreq.keys():
          zeroRowProb += zeroWordFreq[word]
        else:
          zeroRowProb += math.log(1/zeroWordCount)
      zeroProb.append(zeroRowProb)
  return zeroProb

In [0]:
def errorCheck(oneProb, zeroProb, y_train):
  checkerArr = []
  error = 0
  for i in range(25000):
    if oneProb[i]>zeroProb[i]:
      checkerArr.append(1)
    else:
      checkerArr.append(0)
    if y_train[i] != checkerArr[i]:
      error +=1
  return (error/25000)*100

In [0]:
#this is where we check our naive bayes classifier with test set data
one = oneTrainer(x_test, y_test)
zero = zeroTrainer(x_test, y_test)
errorCheck(one, zero, y_test)
accuracy = 0
accuracy = 100 - errorCheck(one, zero, y_test)
print("Accuracy is", accuracy, "%")

Accuracy is 81.27199999999999 %
